In [16]:
import os
import glob

In [17]:
len(os.listdir('data/liver-ultrasound-detection-unzip/labels/val'))

2445

In [18]:
len(os.listdir('data/liver-ultrasound-detection-unzip/images/val'))

4898

In [20]:
# !mkdir data/trainmixval
# !mkdir data/trainmixval/images
# !mkdir data/trainmixval/images/train
# !mkdir data/trainmixval/images/test
# !mkdir data/trainmixval/images/val

# !mkdir data/trainmixval/labels
# !mkdir data/trainmixval/labels/train
# !mkdir data/trainmixval/labels/test
# !mkdir data/trainmixval/labels/val

In [21]:
!cp -r data/liver-ultrasound-detection-unzip/images/test/* data/trainmixval/images/test
!cp -r data/liver-ultrasound-detection-unzip/images/train/* data/trainmixval/images/train
!cp -r data/liver-ultrasound-detection-unzip/images/val/* data/trainmixval/images/val

!cp -r data/liver-ultrasound-detection-unzip/labels/train/* data/trainmixval/labels/train
!cp -r data/liver-ultrasound-detection-unzip/labels/val/* data/trainmixval/labels/val

In [22]:
len(os.listdir('data/trainmixval/images/test'))

5153

In [23]:
len(os.listdir('data/trainmixval/images/train'))

14448

In [24]:
len(os.listdir('data/trainmixval/images/val'))

4898

In [25]:
len(os.listdir('data/trainmixval/labels/train'))

7222

In [26]:
len(os.listdir('data/trainmixval/labels/val'))

2445

In [35]:
import pandas as pd
mapping = pd.read_excel('data/liver-ultrasound-detection-unzip/mapping.xlsx')

In [36]:
mapping

Image File Annotation File   Source              Type
0       24084.jpg       24084.txt  machine  machine_positive
1       97528.jpg       97528.txt  machine  machine_positive
2       54563.jpg       54563.txt  machine  machine_positive
3      115211.jpg      115211.txt  machine  machine_positive
4       71913.jpg       71913.txt  machine  machine_positive
...           ...             ...      ...               ...
19341    1160.jpg             NaN   mobile   mobile_negative
19342     153.jpg             NaN   mobile   mobile_negative
19343  130705.jpg             NaN   mobile   mobile_negative
19344     812.jpg             NaN   mobile   mobile_negative
19345    1410.jpg             NaN   mobile   mobile_negative

[19346 rows x 4 columns]

In [37]:
mapping['Image File'] = mapping['Image File'].apply(lambda x: x.strip())

In [38]:
mapping['type'] = 'train'

In [39]:
for img in os.listdir('data/trainmixval/images/val'):
    mapping['type'][mapping['Image File'] == img] = 'val'

/tmp/ipykernel_20303/3413970268.py:2: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  mapping['type'][mapping['Image File'] == img] = 'val'
/tmp/ipykernel_20303/3413970268.py:2: FutureWarning: ChainedAssignmentError: behaviour will change in p

In [40]:
mapping

Image File Annotation File   Source              Type   type
0       24084.jpg       24084.txt  machine  machine_positive  train
1       97528.jpg       97528.txt  machine  machine_positive  train
2       54563.jpg       54563.txt  machine  machine_positive  train
3      115211.jpg      115211.txt  machine  machine_positive  train
4       71913.jpg       71913.txt  machine  machine_positive    val
...           ...             ...      ...               ...    ...
19341    1160.jpg             NaN   mobile   mobile_negative    val
19342     153.jpg             NaN   mobile   mobile_negative    val
19343  130705.jpg             NaN   mobile   mobile_negative  train
19344     812.jpg             NaN   mobile   mobile_negative  train
19345    1410.jpg             NaN   mobile   mobile_negative    val

[19346 rows x 5 columns]

In [49]:
mapping['type'][mapping['Source'] == 'mobile'].value_counts()

type
val      899
train    449
Name: count, dtype: int64

In [52]:
899 - 600

299

In [55]:
3999 - 3500

499

In [50]:
mapping['type'][mapping['Source'] == 'machine'].value_counts()

type
train    13999
val       3999
Name: count, dtype: int64

In [44]:
mapping['type'][mapping['Image File'] == '24084.jpg'].values[0]

'train'

In [56]:
mapping['Image File'][mapping['type'] == 'val']

4        71913.jpg
5        20584.jpg
8        93028.jpg
14       82131.jpg
18       40502.jpg
           ...    
19337     3978.jpg
19340     4030.jpg
19341     1160.jpg
19342      153.jpg
19345     1410.jpg
Name: Image File, Length: 4898, dtype: object

In [61]:
mapping['Image File'][(mapping['type'] == 'val') & (mapping['Source'] == 'mobile')]

17998    86425.jpg
17999    41608.jpg
18000    99277.jpg
18001    94035.jpg
18002    19339.jpg
           ...    
19337     3978.jpg
19340     4030.jpg
19341     1160.jpg
19342      153.jpg
19345     1410.jpg
Name: Image File, Length: 899, dtype: object

In [70]:
labels_val_path = os.listdir('data/trainmixval/labels/val')
labels_train_path = os.listdir('data/trainmixval/labels/train')

In [72]:
num_val = 1
for img in mapping['Image File'][(mapping['type'] == 'val') & (mapping['Source'] == 'mobile')]:
    if num_val <= 600:
        src_img = 'data/trainmixval/images/val/' + img
        des_img = 'data/trainmixval/images/train/'
        src_lab = 'data/trainmixval/labels/val/' + img[:-4] + '.txt'
        des_lab = 'data/trainmixval/labels/train/'
        !mv {src_img} {des_img}
        if img[:-4] + '.txt' in labels_val_path:
            !mv {src_lab} {des_lab}
    num_val += 1

In [73]:
len(os.listdir('data/trainmixval/images/val'))

4298

In [75]:
num_val = 1
for img in mapping['Image File'][(mapping['type'] == 'val') & (mapping['Source'] == 'machine')]:
    if num_val <= 3500:
        src_img = 'data/trainmixval/images/val/' + img
        des_img = 'data/trainmixval/images/train/'
        src_lab = 'data/trainmixval/labels/val/' + img[:-4] + '.txt'
        des_lab = 'data/trainmixval/labels/train/'
        !mv {src_img} {des_img}
        if img[:-4] + '.txt' in labels_val_path:
            !mv {src_lab} {des_lab}
    num_val += 1

UnboundLocalError: local variable 'child' referenced before assignment

In [76]:
len(os.listdir('data/trainmixval/images/val'))

2404

In [77]:
len(os.listdir('data/trainmixval/labels/val'))

105

In [2]:
# !mkdir data/liver-ultrasound-detection-unzip/images
# !mkdir data/liver-ultrasound-detection-unzip/labels
# !mkdir data/liver-ultrasound-detection-unzip/images/train
# !mkdir data/liver-ultrasound-detection-unzip/labels/train
# !mkdir data/liver-ultrasound-detection-unzip/images/val
# !mkdir data/liver-ultrasound-detection-unzip/labels/val
# !mkdir data/liver-ultrasound-detection-unzip/images/test

# !mv data/liver-ultrasound-detection-unzip/train/train/images/* data/liver-ultrasound-detection-unzip/images/train
# !mv data/liver-ultrasound-detection-unzip/train/train/annotations/* data/liver-ultrasound-detection-unzip/labels/train

# !mv data/liver-ultrasound-detection-unzip/val/val/images/* data/liver-ultrasound-detection-unzip/images/val
# !mv data/liver-ultrasound-detection-unzip/val/val/annotations/* data/liver-ultrasound-detection-unzip/labels/val

# !mv data/liver-ultrasound-detection-unzip/test/test/images/* data/liver-ultrasound-detection-unzip/images/test
# !mv data/liver-ultrasound-detection-unzip/images/test/images/* data/liver-ultrasound-detection-unzip/images/test

# !mkdir data/liver-ultrasound-detection-unzip/datasets
# !mv data/liver-ultrasound-detection-unzip/images data/liver-ultrasound-detection-unzip/datasets
# !mv data/liver-ultrasound-detection-unzip/labels data/liver-ultrasound-detection-unzip/datasets
# !mv data/liver-ultrasound-detection-unzip/datasets/images data/liver-ultrasound-detection-unzip
# !mv data/liver-ultrasound-detection-unzip/datasets/labels data/liver-ultrasound-detection-unzip
# !mkdir data/liver-ultrasound-detection-unzip/images

In [3]:
# !rm -r data/liver-ultrasound-detection-unzip/train
# !rm -r data/liver-ultrasound-detection-unzip/val
# # !rmdir /content/test/test/images
# # !rmdir /content/test/test
# !rm -r data/liver-ultrasound-detection-unzip/test

In [78]:
ROOT = 'data/trainmixval/'

In [79]:
print('Number of train images : ' + str(len(os.listdir(ROOT + 'images/train'))))
print('Number of train labels : ' + str(len(os.listdir(ROOT + 'labels/train'))))

Number of train images : 16942
Number of train labels : 9562


In [80]:
print('Number of val images : ' + str(len(os.listdir(ROOT + 'images/val'))))
print('Number of val labels : ' + str(len(os.listdir(ROOT + 'labels/val'))))

Number of val images : 2404
Number of val labels : 105


In [81]:
print('Number of test images : ' + str(len(os.listdir(ROOT + 'images/test'))))

Number of test images : 5153


In [82]:
import yaml

# Define the data to be written to the YAML file
data = {
    'path': ROOT,
    'train': 'images/train',
    'val': 'images/val',
    'test': 'images/test',
    'names': {
        0: 'FFC',
        1: 'FFS',
        2: 'HCC',
        3: 'cyst',
        4: 'hemangioma',
        5: 'dysplastic',
        6: 'CCA'
    }
}

# Write the data to a YAML file
with open(ROOT + 'data.yml', 'w') as file:
    yaml.dump(data, file, default_flow_style=False, sort_keys=False)

print("YAML file written successfully.")

YAML file written successfully.


In [83]:
from ultralytics import YOLO

# Load a model
model = YOLO('yolov9e.pt')

In [84]:
model.info()

YOLOv9e summary: 1225 layers, 58206592 parameters, 0 gradients, 193.0 GFLOPs


(1225, 58206592, 0, 193.0156544)

In [85]:
results = model.train(data='./data/trainmixval/data.yml', epochs=50, batch=32, device = [0,1,2,3]) 

Ultralytics YOLOv8.1.34 🚀 Python-3.9.19 torch-2.3.0+cu121 CUDA:0 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:1 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:2 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:3 (NVIDIA A100-SXM4-40GB, 40338MiB)
engine/trainer: task=detect, mode=train, model=yolov9e.pt, data=./data/trainmixval/data.yml, epochs=50, time=None, patience=100, batch=32, imgsz=640, save=True, save_period=-1, val_period=1, cache=False, device=[0, 1, 2, 3], workers=8, project=None, name=train39, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=Fals

*****************************************
Setting OMP_NUM_THREADS environment variable for each process to be 1 in default, to avoid your system being overloaded, please further tune the variable for optimal performance in your application as needed. 
*****************************************


Ultralytics YOLOv8.1.34 🚀 Python-3.9.19 torch-2.3.0+cu121 CUDA:0 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:1 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:2 (NVIDIA A100-SXM4-40GB, 40338MiB)
                                                           CUDA:3 (NVIDIA A100-SXM4-40GB, 40338MiB)


[W Utils.hpp:166] Warning: Environment variable NCCL_BLOCKING_WAIT is deprecated; use TORCH_NCCL_BLOCKING_WAIT instead (function getCvarBool)
[W Utils.hpp:166] Warning: Environment variable NCCL_BLOCKING_WAIT is deprecated; use TORCH_NCCL_BLOCKING_WAIT instead (function getCvarBool)
[W Utils.hpp:166] Warning: Environment variable NCCL_BLOCKING_WAIT is deprecated; use TORCH_NCCL_BLOCKING_WAIT instead (function getCvarBool)
[W Utils.hpp:166] Warning: Environment variable NCCL_BLOCKING_WAIT is deprecated; use TORCH_NCCL_BLOCKING_WAIT instead (function getCvarBool)


TensorBoard: Start with 'tensorboard --logdir runs/detect/train39', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=7
Transferred 1805/1811 items from pretrained weights
Freezing layer 'model.42.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks skipped ⚠️, offline and unable to download YOLOv8n. Setting 'amp=True'. If you experience zero-mAP or NaN losses you can disable AMP with amp=False.


...

                   all       2404        113      0.624      0.757      0.722      0.425

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      46/50      12.5G      1.151     0.5996      1.217          3        640: 
                 Class     Images  Instances      Box(P          R      mAP50  


                   all       2404        113      0.667      0.731      0.713      0.412

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      47/50      11.9G      1.094     0.5587       1.21         10        640: W0531 06:30:21.438875 139898235255680 torch/distributed/elastic/agent/server/api.py:741] Received Signals.SIGINT death signal, shutting down workers
W0531 06:30:21.439489 139898235255680 torch/distributed/elastic/multiprocessing/api.py:851] Sending process 17993 closing signal SIGINT
W0531 06:30:21.439666 139898235255680 torch/distributed/elastic/multiprocessing/api.py:851] Sending process 17994 closing signal SIGINT
W0531 06:30:21.439777 139898235255680 torch/distributed/elastic/multiprocessing/api.py:851] Sending process 17995 closing signal SIGINT
W0531 06:30:21.439876 139898235255680 torch/distributed/elastic/multiprocessing/api.py:851] Sending process 17996 closing signal SIGINT
      47/50      11.9G      1.094     0.5587       1.21         10        640: 
[rank1]: Traceback (most recent call last):
[rank1]:   File "/home/ai4095/.config/Ultralytics/DDP/_temp_gq54lx1o140060246096096.py", line 12, in <mo

KeyboardInterrupt: 

In [1]:
from ultralytics import YOLO
model = YOLO('runs/detect/train39/weights/best.pt') #39epoch

In [ ]:
results_test = model.val()

In [ ]:
# results_test = model.test()

In [2]:
import pandas as pd
sample_submission = pd.read_csv('data/liver-ultrasound-detection-unzip/sample_submission.csv')
submission = sample_submission.copy()
submission

Image File              Annotation Label
0          18999  [[281, 183, 339, 266]]   [1]
1         102037  [[263, 171, 359, 263]]   [4]
2         138340   [[85, 235, 178, 333]]   [4]
3         140589                     NaN   NaN
4          20235                     NaN   NaN
...          ...                     ...   ...
5148        3575                     NaN   NaN
5149         190                     NaN   NaN
5150        1404                     NaN   NaN
5151         184                     NaN   NaN
5152        1376                     NaN   NaN

[5153 rows x 3 columns]

In [3]:
sample_submission.loc[~sample_submission['Annotation'].isna().values, 'Annotation']

0                             [[281, 183, 339, 266]]
1                             [[263, 171, 359, 263]]
2                              [[85, 235, 178, 333]]
24      [[270, 195, 335, 253], [268, 264, 316, 286]]
115     [[387, 268, 513, 361], [427, 203, 456, 237]]
1001                                              []
Name: Annotation, dtype: object

In [4]:
index_sample = sample_submission.loc[~sample_submission['Annotation'].isna().values, 'Annotation'].index
index_sample

Index([0, 1, 2, 24, 115, 1001], dtype='int64')

In [21]:
from tqdm.notebook import tqdm, trange
for i in trange(submission.shape[0]):
  if i in index_sample:
      continue
  results = model('data/liver-ultrasound-detection-unzip/images/test/' + str(submission.iloc[i, 0]) + '.jpg', conf=0.475, verbose=False)
  submission.loc[i,'Annotation'] = str(results[0].boxes.xyxy.round().cpu().numpy().astype(int).tolist())
  submission.loc[i,'Label'] = str(results[0].boxes.cls.cpu().numpy().astype(int).tolist())

  0%|          | 0/5153 [00:00<?, ?it/s]

In [22]:
submission

Image File                 Annotation Label
0          18999     [[281, 183, 339, 266]]   [1]
1         102037     [[263, 171, 359, 263]]   [4]
2         138340      [[85, 235, 178, 333]]   [4]
3         140589     [[594, 376, 660, 437]]   [4]
4          20235     [[292, 115, 340, 151]]   [1]
...          ...                        ...   ...
5148        3575                         []    []
5149         190                         []    []
5150        1404  [[1269, 891, 1500, 1078]]   [3]
5151         184                         []    []
5152        1376                         []    []

[5153 rows x 3 columns]

In [23]:
submission.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5153 entries, 0 to 5152
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Image File  5153 non-null   int64 
 1   Annotation  5153 non-null   object
 2   Label       5153 non-null   object
dtypes: int64(1), object(2)
memory usage: 120.9+ KB


In [24]:
print(submission.loc[0, 'Label'] == sample_submission.loc[0, 'Label'])
print(submission.loc[1, 'Label'] == sample_submission.loc[1, 'Label'])
print(submission.loc[2, 'Label'] == sample_submission.loc[2, 'Label'])
print(submission.loc[24, 'Label'] == sample_submission.loc[24, 'Label'])
print(submission.loc[115, 'Label'] == sample_submission.loc[115, 'Label'])
print(submission.loc[1001, 'Label'] == sample_submission.loc[1001, 'Label'])

True
True
True
True
True
True


In [25]:
submission.to_csv('submission_yoloV9e39ep_trainval_conf0475.csv', index = False)

In [106]:
sum(submission['Annotation'] == pd.read_csv('submission_yoloV9e39ep_trainval_conf04.csv')['Annotation'])

5046